# Echogram Examples

In this notebook, we utilize concatenated data from the Pacific hake survey to create multi-frequency and tricolor echograms. These datasets have been enriched with geographical coordinates.

## Significance of Echogram Visualization

Echogram plotting is of utmost importance for various reasons:

- Fisheries scientists use echograms to scroll through a transect of echosounder data, such as those collected during the hake survey on a ship. This allows them to identify dense aggregations of fish.

- Oceanographers find echograms invaluable for scrolling through months' worth of echosounder data from moorings (e.g., OOI) to observe changes in zooplankton daily movements over extended periods (often 24/7).

- Oceanographers often utilize the "tricolor" echogram, which maps three frequencies to RGB colors. This enables them to distinguish between different fish species based on color variations.

- Fisheries scientists can select a specific area on the echogram display to focus on a region of interest and analyze the `Sv` (volume backscattering strength) within that area for fish analysis. Additionally, they may need to export the dataset sliced by the selected box, allowing them to save the specific `Sv` values within that region to a separate file for further analysis or sharing with colleagues.

## Import Packages and Data 

In [1]:
import panel
import xarray as xr
import echoshader

`echoshader` works with datasets which are regularly gridded, and the dimensions are `(channel, echo_range/depth, ping_time)`. The `echo_range` should be the same for the whole dataset. We assume they have been produced by the `echopype`'s `compute_MVBS` function, and have the format as displayed below.

In [2]:
from urllib import request

# Calibratd data is stored in Google Drive
url = 'https://drive.google.com/uc?export=download&id=197D0MW-bHaF6mZLcQwyr4zqyEHIfwsep'

def urllib_download():
    request.urlretrieve(url, 'concatenated_MVBS.nc')

urllib_download() 

# Load sample data for testing
MVBS_ds = xr.open_mfdataset(
    paths="concatenated_MVBS.nc",
    data_vars="minimal",
    coords="minimal",
    combine="by_coords",
)

MVBS_ds

<xarray.Dataset>
Dimensions:            (channel: 4, echo_range: 150, ping_time: 875)
Coordinates:
  * channel            (channel) object 'GPT  18 kHz 009072058c8d 1-1 ES18-11...
  * echo_range         (echo_range) float64 0.0 5.0 10.0 ... 735.0 740.0 745.0
  * ping_time          (ping_time) datetime64[ns] 2017-07-24T19:30:00 ... 201...
    time1              (ping_time) datetime64[ns] dask.array<chunksize=(875,), meta=np.ndarray>
Data variables:
    Sv                 (channel, ping_time, echo_range) float64 dask.array<chunksize=(4, 875, 150), meta=np.ndarray>
    frequency_nominal  (channel) float64 dask.array<chunksize=(4,), meta=np.ndarray>
    longitude          (ping_time) float64 dask.array<chunksize=(875,), meta=np.ndarray>
    latitude           (ping_time) float64 dask.array<chunksize=(875,), meta=np.ndarray>
Attributes:
    processing_software_name:     echopype
    processing_software_version:  0.7.1
    processing_time:              2023-05-30T17:40:45Z
    processing_function:          commongrid.compute_MVBS

## Echogram Demonstration

Users have the flexibility to personalize the default settings of echograms with the following options:

- `channel`: A list of frequency channels to display as stacks.

- `cmap`: This setting allows users to choose a colormap for the echogram plot. Users can opt for built-in colormaps, such as "jet" (explore the gallery [here](https://holoviews.org/user_guide/Colormaps.html)), or input customized colormaps using arrays, like the "EK500" example shown below.

- `vmin`: Set the minimum value for the Sv (volume backscattering strength) range.

- `vmax`: Define the maximum value for the Sv range.

In [3]:
eg = MVBS_ds.eshader.echogram(
    channel = [
        'GPT  18 kHz 009072058c8d 1-1 ES18-11',
        'GPT  38 kHz 009072058146 2-1 ES38B',
        'GPT 120 kHz 00907205a6d0 4-1 ES120-7C',
        ],
    cmap = [
        "#FFFFFF",
        "#9F9F9F", 
        "#5F5F5F", 
        "#0000FF", 
        "#00007F", 
        "#00BF00", 
        "#007F00", 
        "#FFFF00", 
        "#FF7F00", 
        "#FF00BF", 
        "#FF0000", 
        "#A6533C", 
        "#783C28",
    ], 
    vmin = -80, 
    vmax = -30,
)

panel.Row(eg)

There are two control widgets associated with the echograms:

- `colormap`: This widget allows you to adjust the colormap used for the echograms.

- `Sv_range_slider`: This slider widget enables you to control the Sv (volume backscattering strength) range displayed in the echograms.

In [4]:
Sv_range_slider = MVBS_ds.eshader.Sv_range_slider

colormap = MVBS_ds.eshader.colormap

echogram_panel = panel.Row(
    panel.Column(
        Sv_range_slider,
        colormap,
    ),
    eg,
)

echogram_panel

Row
    [0] Column
        [0] EditableRangeSlider(end=-1.63, name='Sv Range Slider', start=-95.05, step=0.01, value=(-80, -30), width=300)
        [1] LiteralInput(name='Colormap', type=(<class 'str'>, ..., value=['#FFFFFF', '#9F9F9F', ...])
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

## Tricolor Echogram Demonstration

To activate tricolor mode, simply set `rgb_composite = True`.

The order of the channel list determines the RGB mapping relationship. For instance, in the example shown below, the tricolor colormap maps the 120kHz channel to the red channel, the 38kHz channel to the green channel, and the 18Hz channel to the blue channel.

In [5]:
tricolor_eg = MVBS_ds.eshader.echogram(
    channel=[
        "GPT 120 kHz 00907205a6d0 4-1 ES120-7C",
        "GPT  38 kHz 009072058146 2-1 ES38B",
        "GPT  18 kHz 009072058c8d 1-1 ES18-11",
    ],
    vmin = -80, 
    vmax = -30,
    rgb_composite = True,
)

panel.Row(tricolor_eg)

Row
    [0] ParamMethod(method, _pane=HoloViews, defer_load=False)

There is only one control widget associated with tricolor echograms:

- `Sv_range_slider`: This slider widget allows you to adjust the Sv (volume backscattering strength) range displayed in the tricolor echograms.

In [6]:
Sv_range_slider = MVBS_ds.eshader.Sv_range_slider

tricolor_echogram_panel = panel.Row(
    Sv_range_slider,
    tricolor_eg,
)

tricolor_echogram_panel

Row
    [0] EditableRangeSlider(end=-1.63, name='Sv Range Slider', start=-95.05, step=0.01, value=(-80, -30), width=300)
    [1] ParamMethod(method, _pane=HoloViews, defer_load=False)

## Box Selection

Users can utilize the `Box Select` feature in the toolbar to define a specific rectangular area on the echogram display and obtain the corresponding dataset.

![image.png](./box_select_example.png)

To clear the selected box and reset the box selection, simply use the `Reset Button`.

![image-2.png](./reset_example.png)

In [7]:
data_from_box_select = MVBS_ds.eshader.get_data_from_box()

## Applying Plot Customizations

Users have the option to input `Holoviews options` to tailor the visualizations according to their preferences.

For more in-depth information on using `Holoviews options`, please refer to this [link](https://holoviews.org/user_guide/Applying_Customizations.html#option-list-syntax).

In [8]:
from holoviews import opts

# image_opts = opts.Image(invert_yaxis=True)
image_opts = opts.Image(cmap='Gray')

eg = MVBS_ds.eshader.echogram(
        channel = ['GPT  38 kHz 009072058146 2-1 ES38B'],
        vmin = -80, 
        vmax = -30,
        opts = image_opts,
)

panel.Row(eg)

Row
    [0] ParamMethod(method, _pane=HoloViews, defer_load=False)